In [ ]:
# get stage and species-specific DEs and check overlap

In [3]:
library(Seurat)
library(dplyr)
library(presto)

In [ ]:
# colors
subs3 = c('aCM', 'vCM', 'immature-CM', 'blood', 'immature-blood', 'macrophage', 'endothelial', 'endocardial',
          'epicardial', 'fibroblast', 'SMC', 'pericyte', 'neural-crest')
subcol3 = c('#fd91a0', '#ff6361', '#ffbab5', '#d68a58', '#e5c185', '#eddfc9', '#011a4d', '#255d8d',
            '#499fcd', '#c2d87a', '#fece52', '#feb94a', '#829aed')

In [4]:
# load integrated data
sc1 = readRDS('chicken_integrated_ssSTACAS.rds')
sc1

An object of class Seurat 
20007 features across 72898 samples within 2 assays 
Active assay: integrated (3000 features, 3000 variable features)
 2 layers present: data, scale.data
 1 other assay present: RNA
 2 dimensional reductions calculated: pca, umap

In [5]:
# get harmonised labels
tab1 = read.delim('chicken_ssSTACAS_celltypes.txt', sep = '\t')
tab1[1,]

species cluster celltype subtype     label         cluster_new
1 chicken 0       CM       immature CM immature-CM_1 c1

In [6]:
mat = sc1@assays$RNA@counts
mat_data = sc1@assays$RNA@data

mtd = sc1@meta.data
mtd$species = 'chicken'
mtd$stage = sc1$orig.ident
mtd$broad_type = tab1$subtype[match(sc1$seurat_clusters, tab1$cluster)]
mtd$cluster = tab1$label[match(sc1$seurat_clusters, tab1$cluster)]
mtd[1,]

orig.ident nCount_RNA nFeature_RNA species
stage23_sample3_AAACCCAAGTAACAGT-1 stage23    5044       2506         chicken
                                   dataset         consensus_type  
stage23_sample3_AAACCCAAGTAACAGT-1 stage23_sample3 Endothelial_cell
                                   integrated_snn_res.1 seurat_clusters stage  
stage23_sample3_AAACCCAAGTAACAGT-1 12                   12              stage23
                                   broad_type  cluster      
stage23_sample3_AAACCCAAGTAACAGT-1 endocardial endocardial_4

In [17]:
id1 = setdiff(1:dim(mtd)[1], which(mtd$broad_type %in% c('blood', 'immature blood', 'macrophage')))
sc2 = CreateSeuratObject(counts = mat[,id1], data = mat_data[,id1], meta.data = mtd[id1,])
sc2

An object of class Seurat 
17007 features across 58340 samples within 1 assay 
Active assay: RNA (17007 features, 0 variable features)
 2 layers present: counts, data

In [20]:
# save
saveRDS(sc2, file = 'chicken_integrated_data_v2.rds')

In [13]:
# get stage-specific markers
Idents(sc2) <- 'stage'
ms = FindAllMarkers(sc2)

Calculating cluster stage23

Calculating cluster stage28

Calculating cluster stage32



In [19]:
temp = sc2@meta.data
head(temp %>% group_by(stage, cluster) %>% reframe(count = n()))

stage   cluster       count
1 stage23 SMC_1           62 
2 stage23 aCM_1         1733 
3 stage23 aCM_2         1329 
4 stage23 endocardial_1 1502 
5 stage23 endocardial_2  512 
6 stage23 endocardial_3  733

In [14]:
ms

p_val       avg_log2FC pct.1 pct.2 p_val_adj cluster
COL1A2             0           -2.4310409 0.195 0.562 0         stage23
HBAD               0           -2.1482565 0.614 0.928 0         stage23
COL1A1             0           -1.8917292 0.218 0.526 0         stage23
HBE1               0           -7.3105472 0.005 0.286 0         stage23
HBA1               0           -1.9879767 0.641 0.913 0         stage23
ACTC1              0            0.8715638 0.783 0.537 0         stage23
DCN                0           -2.2952629 0.108 0.335 0         stage23
ANGPT1             0            1.5366111 0.433 0.229 0         stage23
MAGI2              0           -1.4863380 0.405 0.606 0         stage23
PRTG               0            1.1723533 0.362 0.164 0         stage23
ELN                0           -4.0454292 0.044 0.241 0         stage23
TPM1               0            0.9486697 0.571 0.374 0         stage23
TNNT2              0            0.8504892 0.732 0.536 0         stage23
TTN                0            0.6175517 0.846 0.653 0         stage23
TSHZ2              0           -2.2355790 0.145 0.335 0         stage23
EGFR               0           -2.4425468 0.107 0.297 0         stage23
RBM24              0            0.6884200 0.674 0.496 0         stage23
POSTN              0           -1.1814152 0.507 0.684 0         stage23
DHRS3              0           -1.3889694 0.232 0.409 0         stage23
TNNC1              0            0.6759216 0.840 0.664 0         stage23
CHRM2              0            0.9458329 0.517 0.343 0         stage23
RBPMS2             0            0.7396153 0.520 0.347 0         stage23
PLXNA4             0           -2.8971273 0.090 0.263 0         stage23
KCNH7              0            0.6677465 0.329 0.158 0         stage23
COL3A1             0           -1.9246465 0.150 0.320 0         stage23
ADCYAP1            0            0.8856744 0.442 0.272 0         stage23
TENM4              0           -1.7717739 0.174 0.341 0         stage23
PIGG               0            1.1726403 0.492 0.328 0         stage23
LRRC17             0           -3.7605828 0.020 0.182 0         stage23
MYH15              0            0.3979486 0.765 0.605 0         stage23
⋮                  ⋮           ⋮          ⋮     ⋮     ⋮         ⋮      
RPE65.2            0.008720523  0.1449966 0.009 0.011 1         stage32
TSPAN5             0.008770179  0.2615812 0.263 0.267 1         stage32
MRPS18A            0.008788608  0.1694772 0.153 0.167 1         stage32
MYO1D.1            0.008943252  0.4846925 0.091 0.087 1         stage32
PLEKHG5            0.008947380  0.7824651 0.021 0.018 1         stage32
SMARCAL1           0.008972115  0.1607625 0.075 0.083 1         stage32
DNAJC13            0.009022944  0.1624764 0.165 0.180 1         stage32
STRN.1             0.009030890  0.2257405 0.376 0.395 1         stage32
ABHD1              0.009079101 -0.2330297 0.011 0.014 1         stage32
PLEKHM3            0.009086308  0.1928503 0.174 0.191 1         stage32
BIRC8.1            0.009088311  0.1666306 0.061 0.068 1         stage32
CHST12.1           0.009090698 -0.1202680 0.014 0.017 1         stage32
TMEM19             0.009210768  0.4020822 0.070 0.065 1         stage32
AP3S1.1            0.009256682  0.3367220 0.188 0.187 1         stage32
MMEL1.2            0.009262531  0.6028065 0.090 0.085 1         stage32
METAP1D.1          0.009315874  0.2952655 0.075 0.083 1         stage32
LLGL2              0.009407907  0.2212332 0.122 0.134 1         stage32
ENSGALG00010009605 0.009467044  0.1160425 0.032 0.037 1         stage32
FGGY               0.009493845  0.1405882 0.213 0.232 1         stage32
CUL4B              0.009684661  0.2109726 0.154 0.168 1         stage32
LRIG2              0.009738949  0.1915448 0.045 0.051 1         stage32
RALB               0.009793623  0.2277769 0.113 0.125 1         stage32
CACNA2D3           0.009853541  0.4944361 0.097 0.107 1         stage32
TRIP12.1           0.009863793  0.1862243 0.443 0.467 1    